In [1]:
# 1.2 Details

# You are given four training datasets in the form of csv-files. Your Python program needs to be able to
# independently compile a SQLite database (fle) ideally via sqlalchemy and load the training data into a single five-
# column spreadsheet table in the fle. Its first column depicts the x-values of all functions. Table 1, at the end of
# this subsection, shows you which structure your table is expected to have. The fifty ideal functions, which are also
# provided via a CSV-file, must be loaded into another table. Likewise, the first column depicts the x-values,
# meaning there will be 51 columns overall. Table 2, at end of this subsection, schematically describes what
# structure is expected.

# After the training data and the ideal functions have been loaded into the database, the test data (8) must be
# loaded line-by-line from another CSV-file and ~ if it complies with the compiling criterion ~ matched to one of the
# four functions chosen under i (subsection above). Afterwards, the results need to be saved into another four-
# column-table in the SQLite database. In accordance with table 3 at end of this subsection, this table contains four

# columns with x- and y-values as well as the corresponding chosen ideal function and the related deviation.

# Finally, the training data, the test data, the chosen ideal functions as well as the corresponding / assigned datasets
# are visualized under an appropriately chosen representation of the deviation.

# Please create a Python-program which also fulfils the following criteria:

# Its design is sensibly object-oriented

# It includes at least one inheritance
# ~  Itincludes standard- und user-defined exception handlings

# ~ Forlogical reasons, it makes use of Pandas’ packages as well as data visualization via Bokeh, sqlalchemy,
# as well as others.

# ~ Write unit-tests for all useful elements

# ~ Your code needs to be documented in its entirety and also include Documentation Strings, known as
# “docstrings”

# Table 1: The training data's database table:
# X | V1 (training func) | Y2{training func] | Y3(training func) | Y4(training func)

# x1 yin ya ya1 ya

# xn yin yon yan yan

In [2]:
import pandas as pd
ideal_data = pd.read_csv("ideal.csv")
print(ideal_data.head())

      x        y1        y2        y3        y4        y5        y6        y7  \
0 -20.0 -0.912945  0.408082  9.087055  5.408082 -9.087055  0.912945 -0.839071   
1 -19.9 -0.867644  0.497186  9.132356  5.497186 -9.132356  0.867644 -0.865213   
2 -19.8 -0.813674  0.581322  9.186326  5.581322 -9.186326  0.813674 -0.889191   
3 -19.7 -0.751573  0.659649  9.248426  5.659649 -9.248426  0.751573 -0.910947   
4 -19.6 -0.681964  0.731386  9.318036  5.731386 -9.318036  0.681964 -0.930426   

         y8        y9  ...        y41        y42       y43       y44  \
0 -0.850919  0.816164  ... -40.456474  40.204040  2.995732 -0.008333   
1  0.168518  0.994372  ... -40.233820  40.048590  2.990720 -0.008340   
2  0.612391  1.162644  ... -40.006836  39.890660  2.985682 -0.008347   
3 -0.994669  1.319299  ... -39.775787  39.729824  2.980619 -0.008354   
4  0.774356  1.462772  ... -39.540980  39.565693  2.975530 -0.008361   

         y45       y46       y47       y48       y49       y50  
0  12.995732  5

In [3]:
# Import necessary libraries
import pandas as pd
from sqlalchemy import create_engine, exc
from tabulate import tabulate

# Define an exception class for custom exceptions
class CustomException(Exception):
    pass

# Define a base class for database operations
class Database:
    def __init__(self, db_path):
        self.engine = create_engine(f"sqlite:///{db_path}")
        self.connection = self.engine.connect()

    def create_table(self, table_name, columns):
        try:
            self.connection.execute(f"CREATE TABLE IF NOT EXISTS {table_name} ({', '.join(columns)})")
        except exc.SQLAlchemyError as e:
            raise CustomException(f"Error creating table: {e}")

    def execute_query(self, query):
        try:
            result = self.connection.execute(query)
            return result
        except exc.SQLAlchemyError as e:
            raise CustomException(f"Error executing query: {e}")

# Class for training data
class TrainingData(Database):
    def __init__(self, db_path, csv_path):
        super().__init__(db_path)
        self.data = pd.read_csv(csv_path)

    def load_data(self, table_name):
        try:
            self.create_table(table_name, ["X INTEGER", "V1 REAL", "Y2 REAL", "Y3 REAL", "Y4 REAL"])
            self.data.to_sql(table_name, self.connection, if_exists='replace', index=False)
        except exc.SQLAlchemyError as e:
            raise CustomException(f"Error loading training data: {e}")

# Class for ideal functions
class IdealFunctions(Database):
    def __init__(self, db_path, csv_path):
        super().__init__(db_path)
        self.functions = pd.read_csv(csv_path)

    def load_functions(self, table_name):
        try:
            self.create_table(table_name, ["X INTEGER"] + [f"Func{i} REAL" for i in range(1, 52)])
            self.functions.to_sql(table_name, self.connection, if_exists='replace', index=False)
        except exc.SQLAlchemyError as e:
            raise CustomException(f"Error loading ideal functions: {e}")

# Class for test data
class TestData(Database):
    def __init__(self, db_path, csv_path):
        super().__init__(db_path)
        self.test_data = pd.read_csv(csv_path)

    def create_results_table(self, table_name):
        try:
            self.create_table(table_name, ["X INTEGER", "Y REAL", "ChosenFunction REAL", "Deviation REAL"])
        except exc.SQLAlchemyError as e:
            raise CustomException(f"Error creating Results table: {e}")

    def match_and_save_results(self, training_table, ideal_table, results_table):
        try:
            # Create the Results table if it doesn't exist
            self.create_results_table(results_table)

            # Get the column names for Y1 to Y4 from the training data
            training_columns = [f"Y{i}" for i in range(1, 5)]

            # Loop through each training column to match test data and save results
            for training_column in training_columns:
                query = f"""
                    INSERT INTO {results_table} (X, Y, ChosenFunction, Deviation)
                    SELECT T.X, T.{training_column} AS Y, I.{training_column} AS ChosenFunction, ABS(T.{training_column} - I.{training_column}) AS Deviation
                    FROM {training_table} AS T
                    JOIN {ideal_table} AS I ON T.X = I.X
                """
                self.execute_query(query)

        except exc.SQLAlchemyError as e:
            raise CustomException(f"Error matching and saving results: {e}")

# Main program
if __name__ == "__main__":
    try:
        # Instantiate objects
        training_data = TrainingData("your_database.db", "train.csv")
        ideal_functions = IdealFunctions("your_database.db", "ideal.csv")
        test_data = TestData("your_database.db", "test.csv")

        # Load data into the database
        training_data.load_data("TrainingData")
        ideal_functions.load_functions("IdealFunctions")

        # Match test data and save results
        test_data.match_and_save_results("TrainingData", "IdealFunctions", "Results")

        # Read the results from the database into a DataFrame
        results_df = pd.read_sql("SELECT * FROM Results", test_data.connection)

        # Print Results
        print("Results:")
        print(tabulate(results_df, headers='keys', tablefmt='pretty', showindex=False))

    except CustomException as e:
        print(f"Error: {e}")


Results:
+--------------+---------------+----------------+---------------------+
|      X       |       Y       | ChosenFunction |      Deviation      |
+--------------+---------------+----------------+---------------------+
|    -20.0     |   39.778572   |   -0.9129453   | 40.691517299999994  |
|    -19.9     |   39.604813   |   -0.8676441   |     40.4724571      |
|    -19.8     |   40.09907    |  -0.81367373   | 40.912743729999995  |
|    -19.7     |    40.1511    |  -0.75157344   |     40.90267344     |
|    -19.6     |   39.795662   |   -0.6819636   |     40.4776256      |
|    -19.5     |   39.340855   |  -0.60553986   |     39.94639486     |
|    -19.4     |   39.25246    |  -0.52306575   |     39.77552575     |
|    -19.3     |   38.590164   |  -0.43536535   |     39.02552935     |
|    -19.2     |   38.893463   |  -0.34331492   | 39.236777919999994  |
|    -19.1     |   38.364567   |   -0.2478342   |     38.6124012      |
|    -19.0     |   38.13553    |   -0.1498772   |     3

In [4]:
from tabulate import tabulate

# Assuming you have instantiated the objects and loaded data as in your program

# Print Training Data
print("Training Data:")
print(tabulate(training_data.data, headers='keys', tablefmt='pretty', showindex=False))
print()



Training Data:
+--------------+--------------+-------------+-------------+---------------+
|      x       |      y1      |     y2      |     y3      |      y4       |
+--------------+--------------+-------------+-------------+---------------+
|    -20.0     |  39.778572   |  -40.07859  | -20.214268  |  -0.32491425  |
|    -19.9     |  39.604813   |   -39.784   |  -20.07095  | -0.058819864  |
|    -19.8     |   40.09907   | -40.018845  | -19.906782  |  -0.4518296   |
|    -19.7     |   40.1511    | -39.518402  | -19.389118  |  -0.6120442   |
|    -19.6     |  39.795662   | -39.360065  |  -19.81589  |  -0.3060756   |
|    -19.5     |  39.340855   |  -38.90581  | -19.287113  | -0.062154666  |
|    -19.4     |   39.25246   |  -39.12036  | -19.683708  |  0.026392838  |
|    -19.3     |  38.590164   |  -38.62107  | -19.494537  |  -0.2690418   |
|    -19.2     |  38.893463   | -38.806778  | -19.533716  |  0.08567329   |
|    -19.1     |  38.364567   | -38.354656  |  -18.75372  |  -0.29954198 

In [5]:

# Print Ideal Functions
print("Ideal Functions:")
print(tabulate(ideal_functions.functions, headers='keys', tablefmt='pretty', showindex=False))
print()



Ideal Functions:
+--------------+--------------+--------------+------------+-----------+-------------+---------------+--------------+---------------+--------------+---------------+--------------+-------+---------------+---------------+----------------+---------------+----------------+------------------------+--------+-----------------------+------------------------+------------------------+-------------------------+------------------------+------------+---------------+---------------+--------------+---------------+-----------+--------------+---------------+------------+----------------+----------------+---------------+---------------+---------------+--------------+------------+---------------+-------------+----------------+---------------+------------+---------------+----------------+---------------+--------------+--------------+
|      x       |      y1      |      y2      |     y3     |    y4     |     y5      |      y6       |      y7      |      y8       |      y9      |      y10  

In [6]:
# Print Results
print("Results:")
print(tabulate(results_df, headers='keys', tablefmt='pretty', showindex=False))

Results:
+--------------+---------------+----------------+---------------------+
|      X       |       Y       | ChosenFunction |      Deviation      |
+--------------+---------------+----------------+---------------------+
|    -20.0     |   39.778572   |   -0.9129453   | 40.691517299999994  |
|    -19.9     |   39.604813   |   -0.8676441   |     40.4724571      |
|    -19.8     |   40.09907    |  -0.81367373   | 40.912743729999995  |
|    -19.7     |    40.1511    |  -0.75157344   |     40.90267344     |
|    -19.6     |   39.795662   |   -0.6819636   |     40.4776256      |
|    -19.5     |   39.340855   |  -0.60553986   |     39.94639486     |
|    -19.4     |   39.25246    |  -0.52306575   |     39.77552575     |
|    -19.3     |   38.590164   |  -0.43536535   |     39.02552935     |
|    -19.2     |   38.893463   |  -0.34331492   | 39.236777919999994  |
|    -19.1     |   38.364567   |   -0.2478342   |     38.6124012      |
|    -19.0     |   38.13553    |   -0.1498772   |     3

In [7]:
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource
from bokeh.io import output_notebook


# Assuming results_df is your DataFrame containing the Results table

# Create a Bokeh ColumnDataSource
source = ColumnDataSource(results_df)

# Create a Bokeh figure
p = figure(title="Deviation Visualization", x_axis_label="X", y_axis_label="Deviation")

# Plot a line using X-values and Deviation
p.line(x="X", y="Deviation", line_width=2, source=source, legend_label="Deviation", line_color="navy")

# Add data points
p.circle(x="X", y="Deviation", size=8, source=source, legend_label="Data Points", fill_color="navy", line_color="white")

output_notebook()
show(p, notebook_handle=True)

Loading BokehJS ...